# Modeling

## Load Packages

In [1]:
# TODO: add annotations describing usage of different modules

from operator import mod
from os import getcwd
from os.path import exists, join

import joblib
from sklearn.datasets import fetch_california_housing
from sklearn.impute import SimpleImputer
from sklearn.model_selection import GridSearchCV, train_test_split
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import RobustScaler
from sklearn.svm import SVR
import pandas as pd
import numpy as np
# from ydata_profiling import ProfileReport

from sklearn import preprocessing
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import classification_report, confusion_matrix, ConfusionMatrixDisplay
from sklearn.naive_bayes import BernoulliNB
from sklearn.naive_bayes import GaussianNB
from sklearn.naive_bayes import MultinomialNB
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import accuracy_score, recall_score, precision_score, f1_score
from sklearn.linear_model import LogisticRegression, LinearRegression
import warnings
from sklearn import metrics
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import Normalizer
from sklearn.decomposition import PCA
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import ExtraTreesClassifier
import matplotlib.pyplot as plt
from sklearn.ensemble import  GradientBoostingClassifier
# import xgboost as xgb
import seaborn as sns
from sklearn.metrics import confusion_matrix
from sklearn.svm import SVC, LinearSVC 
from sklearn.neural_network import MLPClassifier
from sklearn.model_selection import KFold

from sklearn.metrics import recall_score

from sklearn import tree
from sklearn.decomposition import PCA, SparsePCA

from sklearn.mixture import GaussianMixture
from sklearn.decomposition import PCA
import json
import pickle
from IPython.display import Image
import warnings

from sklearn.datasets import make_classification
from imblearn.over_sampling import RandomOverSampler
from imblearn.under_sampling import RandomUnderSampler
from imblearn.over_sampling import SMOTE
from collections import Counter

import altair as alt
import random
import warnings

warnings.filterwarnings('ignore')

## Load Data

In [2]:
cdc_survey = pd.read_csv('../../data/cdc_nhanes_survey_responses_clean.csv')

# filter to pregnant moms
cdc_survey_pmom = cdc_survey[cdc_survey['has_been_pregnant'] == 1]
cdc_survey_pmom

SEQN  SMQ681  SMQ690A  SMQ710  SMQ720  SMQ725  SMQ690B  SMQ740  \
8      109284     2.0      NaN     NaN     NaN     NaN      NaN     NaN   
11     109290     2.0      NaN     NaN     NaN     NaN      NaN     NaN   
12     109291     2.0      NaN     NaN     NaN     NaN      NaN     NaN   
15     109295     2.0      NaN     NaN     NaN     NaN      NaN     NaN   
18     109300     2.0      NaN     NaN     NaN     NaN      NaN     NaN   
...       ...     ...      ...     ...     ...     ...      ...     ...   
29140   83700     2.0      NaN     NaN     NaN     NaN      NaN     NaN   
29141   83701     2.0      NaN     NaN     NaN     NaN      NaN     NaN   
29144   83711     2.0      NaN     NaN     NaN     NaN      NaN     NaN   
29146   83717     2.0      NaN     NaN     NaN     NaN      NaN     NaN   
29147   83718     1.0      1.0     5.0     7.0     1.0      NaN     NaN   

       SMQ690C  SMQ770  ...  live_birth_count  age_at_first_birth  \
8          NaN     NaN  ...               4.0                17.0   
11         NaN     NaN  ...               3.0                 NaN   
12         NaN     NaN  ...               4.0                21.0   
15         NaN     NaN  ...               3.0                18.0   
18         NaN     NaN  ...               2.0                30.0   
...        ...     ...  ...               ...                 ...   
29140      NaN     NaN  ...               1.0                 NaN   
29141      NaN     NaN  ...               1.0                 NaN   
29144      NaN     NaN  ...               2.0                27.0   
29146      NaN     NaN  ...               7.0                19.0   
29147      NaN     NaN  ...               2.0                18.0   

       age_at_last_birth  months_since_birth  horomones_not_bc  \
8                   24.0                 NaN               2.0   
11                   NaN                 NaN               2.0   
12                  39.0                 NaN               2.0   
15                  24.0                 NaN               2.0   
18                  33.0                 NaN               2.0   
...                  ...                 ...               ...   
29140               27.0                 NaN               2.0   
29141               26.0                 NaN               2.0   
29144               30.0                 NaN               2.0   
29146               40.0                 NaN               2.0   
29147               25.0                 NaN               1.0   

       smoked_100_cigs  currently_smoke  height_in  weight_lbs  \
8                  2.0              NaN       60.0       178.0   
11                 2.0              NaN       63.0       155.0   
12                 2.0              NaN       64.0       148.0   
15                 2.0              NaN       63.0       137.0   
18                 2.0              NaN       59.0       130.0   
...                ...              ...        ...         ...   
29140              2.0              NaN       64.0       153.0   
29141              2.0              NaN       65.0       160.0   
29144              2.0              NaN       61.0       185.0   
29146              2.0              NaN        NaN        93.0   
29147              1.0              1.0       66.0       165.0   

       attempt_weight_loss_1yr  
8                          1.0  
11                         1.0  
12                         2.0  
15                         2.0  
18                         1.0  
...                        ...  
29140                      2.0  
29141                      2.0  
29144                      NaN  
29146                      2.0  
29147                      NaN  

[7741 rows x 863 columns]

In [3]:
cdc_survey_women = cdc_survey[cdc_survey["is_male"]==0]
cdc_survey_women

SEQN  SMQ681  SMQ690A  SMQ710  SMQ720  SMQ725  SMQ690B  SMQ740  \
0      109264     2.0      NaN     NaN     NaN     NaN      NaN     NaN   
1      109266     2.0      NaN     NaN     NaN     NaN      NaN     NaN   
5      109277     2.0      NaN     NaN     NaN     NaN      NaN     NaN   
6      109279     2.0      NaN     NaN     NaN     NaN      NaN     NaN   
8      109284     2.0      NaN     NaN     NaN     NaN      NaN     NaN   
...       ...     ...      ...     ...     ...     ...      ...     ...   
35651   83645     NaN      NaN     NaN     NaN     NaN      NaN     NaN   
35673   83681     NaN      NaN     NaN     NaN     NaN      NaN     NaN   
35685   83706     NaN      NaN     NaN     NaN     NaN      NaN     NaN   
35689   83710     NaN      NaN     NaN     NaN     NaN      NaN     NaN   
35703   83728     NaN      NaN     NaN     NaN     NaN      NaN     NaN   

       SMQ690C  SMQ770  ...  live_birth_count  age_at_first_birth  \
0          NaN     NaN  ...               NaN                 NaN   
1          NaN     NaN  ...               NaN                 NaN   
5          NaN     NaN  ...               NaN                 NaN   
6          NaN     NaN  ...               NaN                 NaN   
8          NaN     NaN  ...               4.0                17.0   
...        ...     ...  ...               ...                 ...   
35651      NaN     NaN  ...               NaN                 NaN   
35673      NaN     NaN  ...               NaN                 NaN   
35685      NaN     NaN  ...               NaN                 NaN   
35689      NaN     NaN  ...               NaN                 NaN   
35703      NaN     NaN  ...               NaN                 NaN   

       age_at_last_birth  months_since_birth  horomones_not_bc  \
0                    NaN                 NaN               NaN   
1                    NaN                 NaN               2.0   
5                    NaN                 NaN               NaN   
6                    NaN                 NaN               NaN   
8                   24.0                 NaN               2.0   
...                  ...                 ...               ...   
35651                NaN                 NaN               NaN   
35673                NaN                 NaN               NaN   
35685                NaN                 NaN               NaN   
35689                NaN                 NaN               NaN   
35703                NaN                 NaN               NaN   

       smoked_100_cigs  currently_smoke  height_in  weight_lbs  \
0                  NaN              NaN        NaN         NaN   
1                  2.0              NaN       64.0       210.0   
5                  NaN              NaN        NaN         NaN   
6                  NaN              NaN       64.0       122.0   
8                  2.0              NaN       60.0       178.0   
...                ...              ...        ...         ...   
35651              NaN              NaN        NaN         NaN   
35673              NaN              NaN        NaN         NaN   
35685              NaN              NaN        NaN         NaN   
35689              NaN              NaN        NaN         NaN   
35703              NaN              NaN        NaN         NaN   

       attempt_weight_loss_1yr  
0                          NaN  
1                          1.0  
5                          NaN  
6                          2.0  
8                          1.0  
...                        ...  
35651                      NaN  
35673                      NaN  
35685                      NaN  
35689                      NaN  
35703                      NaN  

[18090 rows x 863 columns]

In [4]:
np.mean(cdc_survey['MDD'])

0.04234582423122164

In [5]:
np.mean(cdc_survey_pmom['MDD'])

0.0971450716961633

In [6]:
np.mean(cdc_survey_women['MDD'])

0.056716417910447764

In [7]:
cdc_survey.groupby(['folder'])['MDD'].sum()

folder
2013_2014         404
2015_2016         392
2017_march2020    716
Name: MDD, dtype: int64

In [8]:
cdc_survey_pmom.groupby(['folder'])['MDD'].sum()

folder
2013_2014         204
2015_2016         200
2017_march2020    348
Name: MDD, dtype: int64

### Features to Use

In [9]:
all_columns = [
    # Depression screener
    'little_interest_in_doing_things',
    'feeling_down_depressed_hopeless',
    'trouble_falling_or_staying_asleep',
    'feeling_tired_or_having_little_energy',
    'poor_appetitie_or_overeating',
    'feeling_bad_about_yourself',
    'trouble_concentrating',
    'moving_or_speaking_to_slowly_or_fast',
    'thoughts_you_would_be_better_off_dead',
    'difficult_doing_daytoday_tasks',
    # Alcohol & smoking
    'has_smoked_tabacco_last_5days',
    'alcoholic_drinks_past_12mo', 
    'drank_alc',
    'alc_drinking_freq',
    'alc_per_day',
    'times_with_4or5_alc',
    'times_with_8plus_alc',
    'times_with_12plus_alc',
    '4plus_alc_daily',
    'days_4plus_drinks_occasion',
    #Blood Pressure & Cholesterol
    'high_bp',
    'age_hypertension',
    'hypertension_prescription',
    'high_bp_prescription',
    'high_cholesterol',
    'cholesterol_prescription',
    #Cardiovascular Health
    'chest_discomfort',
    # Diet & Nutrition
    'how_healthy_is_your_diet',    
    'count_lost_10plus_pounds',
    'has_tried_to_lose_weight_12mo', 
    'breastfed',
    'milk_consumption_freq',
    'govmnt_meal_delivery',
    'nonhomemade_meals',
    'fastfood_meals',
    'readytoeat_meals',
    'frozen_pizza',
    #Food Security
    'emergency_food_received',
    'food_stamps_used',
    'wic_benefit_used',
    #Hospital Utilization & Access to Care
    'general_health',
    'regular_healthcare_place',
    'time_since_last_healthcare',
    'overnight_in_hospital',
    'seen_mental_health_professional',
    #Health Insurance
    'have_health_insurance',
    'have_private_insurance',
    'plan_cover_prescriptions',
    #Income
    'family_poverty_level',
    'family_poverty_level_category',
    #Medical Conditions
    'asthma',
    'anemia_treatment',
    'blood_transfusion',
    'arthritis',
    'heart_failure',
    'coronary_heart_disease',
    'angina_pectoris',
    'heart_attack',
    'stroke',
    'thyroid_issues',
    'respiratory_issues',
    'abdominal_pain',
    'gallstones',
    'gallbladder_surgery',
    'cancer',
    'dr_recommend_lose_weight',
    'dr_recommend_exercise',
    'dr_recommend_reduce_salt',
    'dr_recommend_reduce_fat',
    'currently_losing_weight',
    'currently_increase_exercise',
    'currently_reducing_salt',
    'currently_reducing_fat',
    'metal_objects',
    #Occupation
    'hours_worked',
    'over_35_hrs_worked',
    'work_schedule',
    #Physical Activity
    'vigorous_work',
    'walk_or_bicycle',
    'vigorous_recreation',
    'moderate_recreation',
    # Physical health & Medical History
    'count_days_seen_doctor_12mo',
    'duration_last_healthcare_visit',        
    'count_days_moderate_recreational_activity',   
    'count_minutes_moderate_recreational_activity',
    'count_minutes_moderate_sedentary_activity',
    'general_health_condition',    
    'has_diabetes',
    'has_overweight_diagnosis',  
    #Reproductive Health
    'regular_periods',
    'age_last_period',
    'try_pregnancy_1yr',
    'see_dr_fertility',
    'pelvic_infection',
    'pregnant_now',
    'pregnancy_count',
    'diabetes_pregnancy',
    'delivery_count',
    'live_birth_count',
    'age_at_first_birth',
    'age_at_last_birth',
    'months_since_birth',
    'horomones_not_bc',
    #Smoking
    'smoked_100_cigs',
    'currently_smoke',
    #Weight History
    'height_in',
    'weight_lbs',
    'attempt_weight_loss_1yr',
    # Demographic data
    'food_security_level_household',   
    'food_security_level_adult',    
    'monthly_poverty_index_category',
    'monthly_poverty_index',
    'count_hours_worked_last_week',
    'age_in_years',   
    'education_level',
    'is_usa_born',    
    'has_health_insurance',
    'has_health_insurance_gap'   
]
len(all_columns)

118

In [10]:
# find columns where everything is null
# need to delete those
#cdc_survey_pmom = cdc_survey_pmom[all_columns]
#columns = cdc_survey_pmom.columns[cdc_survey_pmom.notnull().any() == False]
#columns

## Preprocessing analysis

### Remove null values

In [11]:
def get_model_data(original_df, 
                   columns, 
                   test_size_to_use=0.2,
                   drop_null_rows=False,
                   null_imputer_strategy='median', # mean, median, most_frequent
                   use_value_scaler=True,
                   use_smote=False):
    """
    Function to build feature & indicator matrices for both train & test.
    """
    
    # add target column (MDD)
    cols_to_use = columns.copy()
    cols_to_use.insert(0, 'MDD')
    
    df_to_use = original_df[cols_to_use]
    
    if drop_null_rows:
        df_to_use.dropna(inplace=True)
    
    # Create test & train data
    x = df_to_use.iloc[:,1:].values
    y = df_to_use['MDD'].values
    
    if not drop_null_rows:
        # SimpleImputer() = fill in missing values
        # note imputer may drop columns if no values exist for it
        imputer = SimpleImputer(strategy=null_imputer_strategy)  
        x = imputer.fit_transform(x)

    # RobustScaler() = scale features to remove outliers
    if use_value_scaler:
        trans = RobustScaler()
        x = trans.fit_transform(x)

    x_train, x_test, y_train, y_test = train_test_split(
        x, 
        y, 
        test_size=test_size_to_use, 
        random_state=42
    ) 
    
    # Technique to de-risk from positive class imbalance
    if use_smote:
        sm = SMOTE(random_state=42)
        x_train, y_train = sm.fit_resample(x_train, y_train)
    
    return x_train, x_test, y_train, y_test

In [12]:
# null_df = cdc_survey_pmom.isnull().sum().to_frame('nulls')
# null_df.reset_index(inplace=True)
# null_df.columns = ['column', 'nulls']


# null_results = null_df[null_df['column'].isin(top_feat)]
# null_results['percent null'] = null_results['nulls']/7741
# null_results.sort_values('percent null', ascending = False)

## Modeling functions

In [13]:
def plot_confusion_matrix(y_test, pred_labels):
    """
    Function that displays a confusion matrix for provided true and predicted classes
    """
    #print(f'cover type 1 and type 2 total correct {np.sum(np.diag(metrics.confusion_matrix(y_test, pred_labels))[:2])}')

    cm = confusion_matrix(y_test, pred_labels)
    disp = ConfusionMatrixDisplay(confusion_matrix=cm)
    fig, ax = plt.subplots(figsize=(5,5))
    disp = disp.plot(include_values=True, cmap='viridis', ax=ax, xticks_rotation='horizontal')    
    plt.grid(False)
    plt.show()
    return

def get_performance_df(label_actual, label_pred, model_name):
    """
    Function to calculate performance metrics for model.
    Includes precision, recal, F1, & support.
    """
    # create classification report
    result_table = classification_report(label_actual, label_pred, output_dict=True)
    result_table = pd.DataFrame.from_dict(result_table)

    # store for later
    accuracies = result_table['accuracy']

    # rename grouping
    result_table.columns = [
        'depressed_no',
        'depressed_yes',
        'accuracy',
        'macro_avg',
        'weighted_avg'
    ]

    # create dataframe with 1 row per grouping
    result_table.drop(labels = 'accuracy', axis = 1, inplace=True)
    result_table = result_table.transpose()
    result_table['accuracy'] = list(accuracies)
    result_table = result_table.reset_index()
    result_table.rename(columns = {'index':'grouping'},inplace=True)
    result_table['model'] = model_name
    result_table = result_table[['model','grouping','precision','recall','f1-score','support','accuracy']]
    return result_table

def baseline_models(
    x_train, 
    y_train, 
    x_test, 
    y_test,
    do_smote=True,
    show_confusion_matrix=False,
    show_score_dataframe=False,
    show_all_groupings=False,
    return_predictions=False):
    """
    Function that trains and makes predictions using 5 of the classifiers went over during the class.
    Meant as a helper function for easier testing of different modeling pipelines.
    """

    #  do_smote
    if do_smote == True:
        sm = SMOTE(random_state=42)
        x_train, y_train = sm.fit_resample(x_train, y_train)

    # K-Nearest Neighbors
    knn = KNeighborsClassifier()
    knn.fit(x_train, y_train)
    pred_labels_knn  = knn.predict(x_test)
    score_knn = get_performance_df(y_test, pred_labels_knn,'Knn')
    
    # Logistic Regression
    lm = LogisticRegression()
    lm.fit(x_train, y_train)
    pred_labels_lr  = lm.predict(x_test)
    score_lr = get_performance_df(y_test, pred_labels_lr,'Logistic Regression')
        
    # Bernoulii Naive Bayes
    bnb = BernoulliNB()
    bnb.fit(x_train, y_train)
    pred_labels_bnb  = bnb.predict(x_test)
    score_bnb = get_performance_df(y_test, pred_labels_bnb,'Bernoulli Naive Bayes')    
        
    # Gaussian Naive Bayes
    gnb = GaussianNB()
    gnb.fit(x_train, y_train)
    pred_labels_gnb  = gnb.predict(x_test)
    score_gnb = get_performance_df(y_test, pred_labels_gnb,'Gaussian Naive Bayes')    

    # Random Forest
    rf = RandomForestClassifier(random_state=0)
    rf.fit(x_train, y_train)
    pred_labels_rf  = rf.predict(x_test)
    predictions_posterior_rf = rf.predict_proba(x_test)
    score_rf = get_performance_df(y_test, pred_labels_rf,'Random Forest')   
    
    #Decision Tree
    dt = DecisionTreeClassifier()
    dt.fit(x_train, y_train)
    pred_labels_dt = dt.predict(x_test)
    score_dt = get_performance_df(y_test, pred_labels_dt,'Decision Tree')

    #Gradient Boosting Classifier
    gb = GradientBoostingClassifier()
    gb.fit(x_train, y_train)
    pred_labels_gb = gb.predict(x_test)
    score_gb = get_performance_df(y_test, pred_labels_gb,'Gradient Boosting Classifier')
    
#     #XGBoost
#     xgboost = xgb.XGBClassifier()
#     xgboost.fit(x_train, y_train)
#     pred_labels_xgboost = gbt.predict(x_test)
#     score_xgboost = get_performance_df(y_test, pred_labels_xgboost,'XGBoost')
    
    # make dataframe with scores
    scores = pd.concat([score_knn, score_lr, score_bnb, score_gnb, score_rf, score_dt, score_gb])
    scores = scores.sort_values(by = 'recall', ascending=False)
    
    if show_score_dataframe:
        display(scores.style.set_table_attributes('style="font-size: 17px"').hide_index())
    
    if show_confusion_matrix:
        print('\nK-Nearest Neighbors Confusion Matrix')
        plot_confusion_matrix(y_test, pred_labels_knn)
        print('Logistic Regression Confusion Matrix')
        plot_confusion_matrix(y_test, pred_labels_lr)
        print('Bernoulli Naive Bayes Confusion Matrix')
        plot_confusion_matrix(y_test, pred_labels_bnb)
        print('Gaussian Naive Bayes Confusion Matrix')
        plot_confusion_matrix(y_test, pred_labels_gnb)
        print('Random Forest Confusion Matrix')
        plot_confusion_matrix(y_test, pred_labels_rf)
        print('Decision Tree Confusion Matrix')
        plot_confusion_matrix(y_test, pred_labels_dt)
        print('Gradient Boosting Confusion Matrix')
        plot_confusion_matrix(y_test, pred_labels_gbt)
#         print('XGBoost Confusion Matrix')
#         plot_confusion_matrix(y_test, pred_labels_xgboost)

    if not show_all_groupings:
        scores = scores[scores['grouping'] == 'macro_avg']
        
    # make dataframe with predictions
    predictions = pd.DataFrame({
        'actuals':y_test,
        'pred_knn':pred_labels_knn,
        'pred_logistic_regression':pred_labels_lr,
        'pred_bernoulli_naive_bayes':pred_labels_bnb,
        'pred_gaussian_naive_bayes':pred_labels_gnb,
        'pred_random_forest':pred_labels_rf,
        'pred_decision_tree':pred_labels_dt,
        'pred_gradient_boosting_classifier':pred_labels_gb
    })

    if return_predictions:
        return scores, predictions
    else:
        return scores

### Women who have been pregnant, depression screening features only

Evaluate the impact of implementing SMOTE for addressing class imbalances, dropping nulls, incorporating additional features, and filtering on performance

In [14]:
x_train, x_test, y_train, y_test = get_model_data(
    original_df = cdc_survey_pmom,
    columns = all_columns[0:10] # just depression screener
)

print(x_train.shape)
print(x_test.shape)
print(y_train.shape)
print(y_test.shape)

(6192, 10)
(1549, 10)
(6192,)
(1549,)


In [15]:
# depression screener only, no dropping nulls, no SMOTE
x_train, x_test, y_train, y_test = get_model_data(
       original_df=cdc_survey_pmom,
       columns = all_columns[0:10],
       test_size_to_use=0.2,
       drop_null_rows=False,
       null_imputer_strategy='median', # mean, median, most_frequent
       use_value_scaler=True,
       use_smote=False)

baseline_model = baseline_models(x_train, y_train, x_test, y_test, do_smote=False)
baseline_model_results = baseline_model[['model','precision','recall','f1-score']]
baseline_model_results['features'] = 'depression only'
baseline_model_results['nulls dropped'] = 'False'
baseline_model_results['SMOTE'] = 'False'

baseline_model = baseline_models(x_train, y_train, x_test, y_test, do_smote=False)
baseline_model_results = baseline_model[['model','precision','recall','f1-score']]
baseline_model_results['features'] = 'depression only'
baseline_model_results['nulls dropped'] = 'False'
baseline_model_results['SMOTE'] = 'False'

baseline_model_with_smote = baseline_models(x_train, y_train, x_test, y_test, do_smote=True)
baseline_model_with_smote_results = baseline_model_with_smote[['model','precision','recall','f1-score']]

baseline_model_with_smote_results['features'] = 'depression only'
baseline_model_with_smote_results['nulls dropped'] = 'False'
baseline_model_with_smote_results['SMOTE'] = 'True'


# depression screener only, dropping nulls, no SMOTE
x_train, x_test, y_train, y_test = get_model_data(
       original_df=cdc_survey_pmom,
       columns = all_columns[0:10],
       test_size_to_use=0.2,
       drop_null_rows=True,
       null_imputer_strategy='median', # mean, median, most_frequent
       use_value_scaler=True,
       use_smote=False)

baseline_model_dropnull = baseline_models(x_train, y_train, x_test, y_test, do_smote=False)
baseline_model_dropnull_results= baseline_model_dropnull[['model','precision','recall','f1-score']]

baseline_model_dropnull_results['features'] = 'depression only'
baseline_model_dropnull_results['nulls dropped'] = 'True'
baseline_model_dropnull_results['SMOTE'] = 'False'

baseline_model_dropnull_SMOTE = baseline_models(x_train, y_train, x_test, y_test, do_smote=True)
baseline_model_dropnull_SMOTE_results = baseline_model_dropnull_SMOTE[['model','precision','recall','f1-score']]

baseline_model_dropnull_SMOTE_results['features'] = 'depression only'
baseline_model_dropnull_SMOTE_results['nulls dropped'] = 'True'
baseline_model_dropnull_SMOTE_results['SMOTE'] = 'True'


### All women, depression screening features only

In [16]:
# depression screener only, no dropping nulls, no SMOTE
x_train, x_test, y_train, y_test = get_model_data(
       original_df=cdc_survey_women,
       columns = all_columns[0:10],
       test_size_to_use=0.2,
       drop_null_rows=False,
       null_imputer_strategy='median', # mean, median, most_frequent
       use_value_scaler=True,
       use_smote=False)

baseline_model = baseline_models(x_train, y_train, x_test, y_test, do_smote=False)
baseline_model_results_women = baseline_model[['model','precision','recall','f1-score']]
baseline_model_results_women['features'] = 'depression only'
baseline_model_results_women['nulls dropped'] = 'False'
baseline_model_results_women['SMOTE'] = 'False'

baseline_model_with_smote = baseline_models(x_train, y_train, x_test, y_test, do_smote=True)
baseline_model_with_smote_results_women = baseline_model_with_smote[['model','precision','recall','f1-score']]

baseline_model_with_smote_results_women['features'] = 'depression only'
baseline_model_with_smote_results_women['nulls dropped'] = 'False'
baseline_model_with_smote_results_women['SMOTE'] = 'True'

# depression screener only, dropping nulls, no SMOTE
x_train, x_test, y_train, y_test = get_model_data(
       original_df=cdc_survey_women,
       columns = all_columns[0:10],
       test_size_to_use=0.2,
       drop_null_rows=True,
       null_imputer_strategy='median', # mean, median, most_frequent
       use_value_scaler=True,
       use_smote=False)

baseline_model_dropnull = baseline_models(x_train, y_train, x_test, y_test, do_smote=False)
baseline_model_dropnull_results_women= baseline_model_dropnull[['model','precision','recall','f1-score']]

baseline_model_dropnull_results_women['features'] = 'depression only'
baseline_model_dropnull_results_women['nulls dropped'] = 'True'
baseline_model_dropnull_results_women['SMOTE'] = 'False'

baseline_model_dropnull_SMOTE = baseline_models(x_train, y_train, x_test, y_test, do_smote=True)
baseline_model_dropnull_SMOTE_results_women = baseline_model_dropnull_SMOTE[['model','precision','recall','f1-score']]

baseline_model_dropnull_SMOTE_results_women['features'] = 'depression only'
baseline_model_dropnull_SMOTE_results_women['nulls dropped'] = 'True'
baseline_model_dropnull_SMOTE_results_women['SMOTE'] = 'True'

### Top identified features

Using the top features only performs better with baseline models compared to using depression screener only features. 
Including SMOTE and/or dropping null values decreases performance.

In [17]:
top_feat = ['times_with_12plus_alc',
 'seen_mental_health_professional',
 'count_days_seen_doctor_12mo',
 'count_lost_10plus_pounds',
 'arthritis',
 'horomones_not_bc',
 'is_usa_born',
 'times_with_8plus_alc',
 'time_since_last_healthcare',
 'duration_last_healthcare_visit',
 'work_schedule',
 'age_in_years',
 'regular_periods',
 'count_minutes_moderate_sedentary_activity',
 'emergency_food_received',
 'high_bp',
 'dr_recommend_exercise',
 'metal_objects',
 'drank_alc',
 'cholesterol_prescription',
 'smoked_100_cigs',
 'vigorous_recreation',
 'dr_recommend_lose_weight',
 'cancer',
 'chest_discomfort',
 'has_health_insurance',
 'have_health_insurance',
 'weight_lbs',
 'high_cholesterol']


high_null_feat = ['times_with_12plus_alc',
                 'duration_last_healthcare_visit',
                 'time_since_last_healthcare',
                 'count_days_seen_doctor_12mo']


top_feat_drop = [feat for feat in top_feat if feat not in high_null_feat]

### Pregnant women, top features only

In [18]:
# top feat only, no dropping nulls, no SMOTE

x_train, x_test, y_train, y_test = get_model_data(
       original_df=cdc_survey_pmom,
       columns = top_feat_drop,
       test_size_to_use=0.2,
       drop_null_rows=False,
       null_imputer_strategy='median', # mean, median, most_frequent
       use_value_scaler=True,
       use_smote=False)

baseline_model = baseline_models(x_train, y_train, x_test, y_test, do_smote=False)
baseline_model_top_results = baseline_model[['model','precision','recall','f1-score']]

baseline_model_top_results['features'] = 'top feat'
baseline_model_top_results['nulls dropped'] = 'False'
baseline_model_top_results['SMOTE'] = 'False'


baseline_model_with_smote = baseline_models(x_train, y_train, x_test, y_test, do_smote=True)
baseline_model_with_smote_top_results = baseline_model_with_smote[['model','precision','recall','f1-score']]

baseline_model_with_smote_top_results['features'] = 'top feat'
baseline_model_with_smote_top_results['nulls dropped'] = 'False'
baseline_model_with_smote_top_results['SMOTE'] = 'True'

# top feat only, dropping nulls, no SMOTE

x_train, x_test, y_train, y_test = get_model_data(
       original_df=cdc_survey_pmom,
       columns = top_feat_drop,
       test_size_to_use=0.2,
       drop_null_rows=True,
       null_imputer_strategy='median', # mean, median, most_frequent
       use_value_scaler=True,
       use_smote=False)

baseline_model_dropnull = baseline_models(x_train, y_train, x_test, y_test, do_smote=False)
baseline_model_dropnull_top_results = baseline_model_dropnull[['model','precision','recall','f1-score']]

baseline_model_dropnull_top_results['features'] = 'top feat'
baseline_model_dropnull_top_results['nulls dropped'] = 'True'
baseline_model_dropnull_top_results['SMOTE'] = 'False'


baseline_model_dropnull_SMOTE = baseline_models(x_train, y_train, x_test, y_test, do_smote=True)
baseline_model_dropnull_SMOTE_top_results = baseline_model_dropnull_SMOTE[['model','precision','recall','f1-score']]

baseline_model_dropnull_SMOTE_top_results['features'] = 'top feat'
baseline_model_dropnull_SMOTE_top_results['nulls dropped'] = 'True'
baseline_model_dropnull_SMOTE_top_results['SMOTE'] = 'True'

### All women, top features only

In [19]:
# top feat only, no dropping nulls, no SMOTE

x_train, x_test, y_train, y_test = get_model_data(
       original_df=cdc_survey_women,
       columns = top_feat_drop,
       test_size_to_use=0.2,
       drop_null_rows=False,
       null_imputer_strategy='median', # mean, median, most_frequent
       use_value_scaler=True,
       use_smote=False)

baseline_model = baseline_models(x_train, y_train, x_test, y_test, do_smote=False)
baseline_model_top_results_women = baseline_model[['model','precision','recall','f1-score']]

baseline_model_top_results_women['features'] = 'top feat'
baseline_model_top_results_women['nulls dropped'] = 'False'
baseline_model_top_results_women['SMOTE'] = 'False'


baseline_model_with_smote = baseline_models(x_train, y_train, x_test, y_test, do_smote=True)
baseline_model_with_smote_top_results_women = baseline_model_with_smote[['model','precision','recall','f1-score']]

baseline_model_with_smote_top_results_women['features'] = 'top feat'
baseline_model_with_smote_top_results_women['nulls dropped'] = 'False'
baseline_model_with_smote_top_results_women['SMOTE'] = 'True'


# top feat only, dropping nulls, no SMOTE

x_train, x_test, y_train, y_test = get_model_data(
       original_df=cdc_survey_women,
       columns = top_feat_drop,
       test_size_to_use=0.2,
       drop_null_rows=True,
       null_imputer_strategy='median', # mean, median, most_frequent
       use_value_scaler=True,
       use_smote=False)


baseline_model_dropnull = baseline_models(x_train, y_train, x_test, y_test, do_smote=False)
baseline_model_dropnull_top_results_women = baseline_model_dropnull[['model','precision','recall','f1-score']]

baseline_model_dropnull_top_results_women['features'] = 'top feat'
baseline_model_dropnull_top_results_women['nulls dropped'] = 'True'
baseline_model_dropnull_top_results_women['SMOTE'] = 'False'



baseline_model_dropnull_SMOTE = baseline_models(x_train, y_train, x_test, y_test, do_smote=True)
baseline_model_dropnull_SMOTE_top_results_women = baseline_model_dropnull_SMOTE[['model','precision','recall','f1-score']]

baseline_model_dropnull_SMOTE_top_results_women['features'] = 'top feat'
baseline_model_dropnull_SMOTE_top_results_women['nulls dropped'] = 'True'
baseline_model_dropnull_SMOTE_top_results_women['SMOTE'] = 'True'

### Top feat + depression

### Pregnant women, top features only

In [20]:
combined_feat = top_feat_drop + all_columns[0:10]

In [21]:
# combined feat, no dropping nulls, no SMOTE

x_train, x_test, y_train, y_test = get_model_data(
       original_df=cdc_survey_pmom,
       columns = combined_feat,
       test_size_to_use=0.2,
       drop_null_rows=False,
       null_imputer_strategy='median', # mean, median, most_frequent
       use_value_scaler=True,
       use_smote=False)


baseline_model = baseline_models(x_train, y_train, x_test, y_test, do_smote=False)
baseline_model_combine_results = baseline_model[['model','precision','recall','f1-score']]

baseline_model_combine_results['features'] = 'top feat+depression'
baseline_model_combine_results['nulls dropped'] = 'False'
baseline_model_combine_results['SMOTE'] = 'False'


baseline_model_with_smote = baseline_models(x_train, y_train, x_test, y_test, do_smote=True)
baseline_model_with_smote_combine_results = baseline_model_with_smote[['model','precision','recall','f1-score']]

baseline_model_with_smote_combine_results['features'] = 'top feat+depression'
baseline_model_with_smote_combine_results['nulls dropped'] = 'False'
baseline_model_with_smote_combine_results['SMOTE'] = 'True'

# combined only, dropping nulls, no SMOTE

x_train, x_test, y_train, y_test = get_model_data(
       original_df=cdc_survey_pmom,
       columns = combined_feat,
       test_size_to_use=0.2,
       drop_null_rows=True,
       null_imputer_strategy='median', # mean, median, most_frequent
       use_value_scaler=True,
       use_smote=False)

baseline_model_dropnull = baseline_models(x_train, y_train, x_test, y_test, do_smote=False)
baseline_model_dropnull_combine_results = baseline_model_dropnull[['model','precision','recall','f1-score']]

baseline_model_dropnull_combine_results['features'] = 'top feat+depression'
baseline_model_dropnull_combine_results['nulls dropped'] = 'True'
baseline_model_dropnull_combine_results['SMOTE'] = 'False'



baseline_model_dropnull_SMOTE = baseline_models(x_train, y_train, x_test, y_test, do_smote=True)
baseline_model_dropnull_SMOTE_combine_results = baseline_model_dropnull_SMOTE[['model','precision','recall','f1-score']]

baseline_model_dropnull_SMOTE_combine_results['features'] = 'top feat+depression'
baseline_model_dropnull_SMOTE_combine_results['nulls dropped'] = 'True'
baseline_model_dropnull_SMOTE_combine_results['SMOTE'] = 'True'

### All women, top features only

In [22]:
# combined feat, no dropping nulls, no SMOTE

x_train, x_test, y_train, y_test = get_model_data(
       original_df=cdc_survey_women,
       columns = combined_feat,
       test_size_to_use=0.2,
       drop_null_rows=False,
       null_imputer_strategy='median', # mean, median, most_frequent
       use_value_scaler=True,
       use_smote=False)


baseline_model = baseline_models(x_train, y_train, x_test, y_test, do_smote=False)
baseline_model_combine_results_women = baseline_model[['model','precision','recall','f1-score']]

baseline_model_combine_results_women['features'] = 'top feat+depression'
baseline_model_combine_results_women['nulls dropped'] = 'False'
baseline_model_combine_results_women['SMOTE'] = 'False'


baseline_model_with_smote = baseline_models(x_train, y_train, x_test, y_test, do_smote=True)
baseline_model_with_smote_combine_results_women = baseline_model_with_smote[['model','precision','recall','f1-score']]

baseline_model_with_smote_combine_results_women['features'] = 'top feat+depression'
baseline_model_with_smote_combine_results_women['nulls dropped'] = 'False'
baseline_model_with_smote_combine_results_women['SMOTE'] = 'True'


# combined only, dropping nulls, no SMOTE

x_train, x_test, y_train, y_test = get_model_data(
       original_df=cdc_survey_women,
       columns = combined_feat,
       test_size_to_use=0.2,
       drop_null_rows=True,
       null_imputer_strategy='median', # mean, median, most_frequent
       use_value_scaler=True,
       use_smote=False)


baseline_model_dropnull = baseline_models(x_train, y_train, x_test, y_test, do_smote=False)
baseline_model_dropnull_combine_results_women = baseline_model_dropnull[['model','precision','recall','f1-score']]

baseline_model_dropnull_combine_results_women['features'] = 'top feat+depression'
baseline_model_dropnull_combine_results_women['nulls dropped'] = 'True'
baseline_model_dropnull_combine_results_women['SMOTE'] = 'False'


baseline_model_dropnull_SMOTE = baseline_models(x_train, y_train, x_test, y_test, do_smote=True)
baseline_model_dropnull_SMOTE_combine_results_women = baseline_model_dropnull_SMOTE[['model','precision','recall','f1-score']]

baseline_model_dropnull_SMOTE_combine_results_women['features'] = 'top feat+depression'
baseline_model_dropnull_SMOTE_combine_results_women['nulls dropped'] = 'True'
baseline_model_dropnull_SMOTE_combine_results_women['SMOTE'] = 'True'

In [23]:
#Pregnant women
merge_results=pd.concat([baseline_model_results,
                        baseline_model_with_smote_results,
                        baseline_model_dropnull_results,
                        baseline_model_dropnull_SMOTE_results,
                        baseline_model_top_results,
                        baseline_model_with_smote_top_results,
                        baseline_model_dropnull_top_results,
                        baseline_model_dropnull_SMOTE_top_results,
                        baseline_model_combine_results,
                        baseline_model_with_smote_combine_results,
                        baseline_model_dropnull_combine_results,
                        baseline_model_dropnull_SMOTE_combine_results])

# chart_df = merge_results[merge_results['features']=='depression only']
chart_df = merge_results

line=alt.Chart(chart_df).mark_line(size=1).encode(
    x=alt.X('features',
           sort=['top feat','depression only','top feat+depression']),
    y=alt.Y('recall', title='Recall', scale=alt.Scale(domain=[0, .82])),
    color='model:N'
).properties(
                width=200,
                height=200
                )

points=alt.Chart(chart_df).mark_point().encode(
    x=alt.X('features',
           sort=['top feat','depression only','top feat+depression']),
    y=alt.Y('recall', title='Recall', scale=alt.Scale(domain=[0, .82])),
    color='model:N')


recall = alt.layer(line, points, data=chart_df).facet(row='SMOTE:N',
                                                     column='nulls dropped')
recall

alt.FacetChart(...)

In [24]:
merge_results.sort_values('recall', ascending=False)

model  precision    recall  f1-score  \
2            Logistic Regression   0.596383  0.714536  0.598440   
2           Gaussian Naive Bayes   0.597451  0.714269  0.601114   
2            Logistic Regression   0.586135  0.699520  0.580058   
2           Gaussian Naive Bayes   0.626397  0.695179  0.646847   
2            Logistic Regression   0.592019  0.693521  0.597918   
..                           ...        ...       ...       ...   
2            Logistic Regression   0.409091  0.409091  0.409091   
2   Gradient Boosting Classifier   0.409091  0.409091  0.409091   
2                            Knn   0.445455  0.397727  0.390991   
2          Bernoulli Naive Bayes   0.400000  0.363636  0.380952   
2                            Knn   0.408497  0.357143  0.346667   

               features nulls dropped  SMOTE  
2   top feat+depression         False   True  
2   top feat+depression         False   True  
2              top feat         False   True  
2   top feat+depression         False  False  
2       depression only         False   True  
..                  ...           ...    ...  
2   top feat+depression          True  False  
2   top feat+depression          True  False  
2   top feat+depression          True   True  
2   top feat+depression          True  False  
2              top feat          True   True  

[84 rows x 7 columns]

In [25]:
#All women
merge_results_women=pd.concat([baseline_model_results_women,
                        baseline_model_with_smote_results_women,
                        baseline_model_dropnull_results_women,
                        baseline_model_dropnull_SMOTE_results_women,
                        baseline_model_top_results_women,
                        baseline_model_with_smote_top_results_women,
                        baseline_model_dropnull_top_results_women,
                        baseline_model_dropnull_SMOTE_top_results_women,
                        baseline_model_combine_results_women,
                        baseline_model_with_smote_combine_results_women,
                        baseline_model_dropnull_combine_results_women,
                        baseline_model_dropnull_SMOTE_combine_results_women])

# chart_df = merge_results[merge_results['features']=='depression only']
chart_df = merge_results_women

line=alt.Chart(chart_df).mark_line(size=1).encode(
    x=alt.X('features',
           sort=['top feat','depression only','top feat+depression']),
    y=alt.Y('recall', title='Recall', scale=alt.Scale(domain=[0, .82])),
    color='model:N'
).properties(
                width=200,
                height=200
                )

points=alt.Chart(chart_df).mark_point().encode(
    x=alt.X('features',
           sort=['top feat','depression only','top feat+depression']),
    y=alt.Y('recall', title='Recall', scale=alt.Scale(domain=[0, .82])),
    color='model:N')


recall_women = alt.layer(line, points, data=chart_df).facet(row='SMOTE:N',
                                                     column='nulls dropped')
recall_women

alt.FacetChart(...)

In [26]:
merge_results_women.sort_values('recall', ascending=False)

model  precision    recall  f1-score             features  \
2    Logistic Regression   0.597530  0.805429  0.607768  top feat+depression   
2   Gaussian Naive Bayes   0.595673  0.789997  0.607738  top feat+depression   
2    Logistic Regression   0.582634  0.781079  0.577798             top feat   
2   Gaussian Naive Bayes   0.606959  0.780855  0.631011  top feat+depression   
2   Gaussian Naive Bayes   0.578892  0.773846  0.569747             top feat   
..                   ...        ...       ...       ...                  ...   
2                    Knn   0.471053  0.435294  0.381887             top feat   
2   Gaussian Naive Bayes   0.462662  0.432353  0.290909             top feat   
2          Decision Tree   0.423077  0.423077  0.423077  top feat+depression   
2          Decision Tree   0.424242  0.411765  0.417910             top feat   
2          Decision Tree   0.421875  0.397059  0.409091             top feat   

   nulls dropped  SMOTE  
2          False   True  
2          False   True  
2          False   True  
2          False  False  
2          False   True  
..           ...    ...  
2           True   True  
2           True  False  
2           True   True  
2           True  False  
2           True   True  

[84 rows x 7 columns]

### Undersampling

Small differences in performance observed between evaluated class imbalance techniques.
RandomOverSampler yields highest recall value for the seven baseline models.

In [27]:
dep_screener_cols = [
    'little_interest_in_doing_things',
    'feeling_down_depressed_hopeless',
    'trouble_falling_or_staying_asleep',
    'feeling_tired_or_having_little_energy',
    'poor_appetitie_or_overeating',
    'feeling_bad_about_yourself',
    'trouble_concentrating',
    'moving_or_speaking_to_slowly_or_fast',
    'thoughts_you_would_be_better_off_dead',
    'difficult_doing_daytoday_tasks'
]

In [28]:
model_features_opt1 = dep_screener_cols + ['times_with_12plus_alc',
    'seen_mental_health_professional',
    'count_days_seen_doctor_12mo',
    'count_lost_10plus_pounds',
    'arthritis',
    'horomones_not_bc',
    'is_usa_born',
    'times_with_8plus_alc',
    'time_since_last_healthcare',
    'duration_last_healthcare_visit',
    'work_schedule',
    'age_in_years',
    'regular_periods',
    'count_minutes_moderate_sedentary_activity',
    'emergency_food_received',
    'high_bp',
    'dr_recommend_exercise',
    'metal_objects',
    'drank_alc',
    'cholesterol_prescription',
    'smoked_100_cigs',
    'vigorous_recreation',
    'dr_recommend_lose_weight',
    'cancer',
    'chest_discomfort',
    'have_health_insurance',
    'weight_lbs',
    'high_cholesterol']
len(model_features_opt1)

38

In [29]:
model_features_opt2 = dep_screener_cols + ['seen_mental_health_professional',
 'times_with_12plus_alc',
 'duration_last_healthcare_visit',
 'time_since_last_healthcare',
 'cholesterol_prescription',
 'high_cholesterol',
 'age_in_years',
 'horomones_not_bc',
 'times_with_8plus_alc',
 'months_since_birth',
 'arthritis',
 'high_bp',
 'regular_periods',
 'moderate_recreation',
 'thyroid_issues',
 'vigorous_recreation',
 'stroke',
 'is_usa_born',
 'asthma']
len(model_features_opt2)

29

In [30]:
combined_feat_fixed = [col for col in combined_feat if col != 'has_health_insurance']
len(combined_feat_fixed)

34

# Hyperparam data split

In [31]:
cdc_survey_pmom_copy = cdc_survey_pmom.copy()
cdc_survey_pmom_copy['null_depression_feats'] = (cdc_survey_pmom_copy[dep_screener_cols] ==0).sum(axis=1)

cdc_survey_pmom_copy = cdc_survey_pmom_copy[cdc_survey_pmom_copy['null_depression_feats'] < 9]


# combined feat, no dropping nulls, yes SMOTE

x_train, x_test, y_train, y_test = get_model_data(
       original_df=cdc_survey_pmom_copy,
       columns = model_features_opt1, #model_features_opt1,#combined_feat_fixed,
       test_size_to_use=0.2,
       drop_null_rows=False,
       null_imputer_strategy='mean',#'most_frequent', # mean, median, most_frequent
       use_value_scaler=True,
       use_smote=False)

rus = RandomUnderSampler(random_state=42, replacement = True)
x_rus, y_rus = rus.fit_resample(x_train,y_train)
print(Counter(y_train))
print(Counter(y_rus))

Counter({0: 3024, 1: 491})
Counter({0: 491, 1: 491})


In [32]:
baseline_model_rus = baseline_models(x_rus, y_rus, x_test, y_test, do_smote=False)
baseline_model_rus[['model','precision','recall','f1-score']]


model  precision    recall  f1-score
2                 Random Forest   0.630156  0.733370  0.618975
2           Logistic Regression   0.635900  0.727426  0.641200
2  Gradient Boosting Classifier   0.629175  0.723932  0.627114
2          Gaussian Naive Bayes   0.608494  0.697922  0.585744
2                           Knn   0.602623  0.675474  0.597958
2         Bernoulli Naive Bayes   0.601225  0.672579  0.596789
2                 Decision Tree   0.590735  0.668640  0.550181

In [33]:
from imblearn.under_sampling import TomekLinks

tomek = TomekLinks()
x_tl, y_tl = tomek.fit_resample(x_train,y_train)
print(Counter(y_train))
print(Counter(y_tl))

Counter({0: 3024, 1: 491})
Counter({0: 2907, 1: 491})


In [34]:
baseline_model_tl = baseline_models(x_tl, y_tl, x_test, y_test, do_smote=False)
baseline_model_tl[['model','precision','recall','f1-score']]


model  precision    recall  f1-score
2          Gaussian Naive Bayes   0.626973  0.711787  0.630949
2         Bernoulli Naive Bayes   0.633257  0.651740  0.640994
2  Gradient Boosting Classifier   0.727693  0.592934  0.615268
2           Logistic Regression   0.748591  0.592069  0.615202
2                 Decision Tree   0.563888  0.569297  0.566187
2                 Random Forest   0.719319  0.567746  0.581190
2                           Knn   0.668302  0.562333  0.573114

In [35]:
from imblearn.under_sampling import NearMiss

nm = NearMiss()
x_nm, y_nm = nm.fit_resample(x_train, y_train)
print(Counter(y_train))
print(Counter(y_nm))

Counter({0: 3024, 1: 491})
Counter({0: 491, 1: 491})


In [36]:
baseline_model_nm = baseline_models(x_nm, y_nm, x_test, y_test, do_smote=False)
baseline_model_nm[['model','precision','recall','f1-score']]


model  precision    recall  f1-score
2           Logistic Regression   0.600659  0.687928  0.548927
2  Gradient Boosting Classifier   0.573361  0.609864  0.398866
2                           Knn   0.555528  0.601957  0.470328
2         Bernoulli Naive Bayes   0.559173  0.601324  0.434287
2                 Random Forest   0.568206  0.597009  0.379867
2          Gaussian Naive Bayes   0.554486  0.592340  0.425471
2                 Decision Tree   0.553911  0.577122  0.370397

### Oversampling

In [37]:
ros = RandomOverSampler(random_state=42)
x_ros, y_ros = ros.fit_resample(x_train,y_train)
print(Counter(y_train))
print(Counter(y_ros))

Counter({0: 3024, 1: 491})
Counter({0: 3024, 1: 3024})


In [38]:
baseline_model_ros = baseline_models(x_ros, y_ros, x_test, y_test, do_smote=False)
print('model_features_opt1')
baseline_model_ros[['model','precision','recall','f1-score']]

model_features_opt1


model  precision    recall  f1-score
2  Gradient Boosting Classifier   0.658849  0.745994  0.675214
2           Logistic Regression   0.637796  0.729456  0.644126
2          Gaussian Naive Bayes   0.599621  0.681606  0.575623
2         Bernoulli Naive Bayes   0.601771  0.673255  0.597695
2                           Knn   0.593529  0.643176  0.598552
2                 Decision Tree   0.598941  0.597791  0.598357
2                 Random Forest   0.734144  0.581355  0.600489

# GBC

In [39]:
gbc = GradientBoostingClassifier(
    learning_rate=0.1,
    loss='log_loss',
    max_depth=3,
    max_features=None,#'log2',
    criterion='squared_error', #'friedman_mse'
    n_estimators=100,
    # min_samples_split=5,
    # min_samples_leaf=2,
    warm_start=True,
    # validation_fraction=0.2,
    # n_iter_no_change=1
    random_state=42,
    
)

gbc.fit(x_ros, y_ros)
pred_labels = [x.round() for x in gbc.predict(x_ros)]
df_cls_rpt = pd.DataFrame(
    classification_report(
        y_ros, 
        pred_labels, 
        target_names=['not depressed', 'depressed'], 
        output_dict=True
    )
).rename_axis('metric')\
.reset_index()
print('Train: Gradient Boosting Classifer')
display(df_cls_rpt)

gbc.fit(x_ros, y_ros)
pred_labels = [x.round() for x in gbc.predict(x_test)]
df_cls_rpt = pd.DataFrame(
    classification_report(
        y_test, 
        pred_labels, 
        target_names=['not depressed', 'depressed'], 
        output_dict=True
    )
).rename_axis('metric')\
.reset_index()
print('Test: Gradient Boosting Classifer')
df_cls_rpt

Train: Gradient Boosting Classifer


metric  not depressed    depressed  accuracy    macro avg  weighted avg
0  precision       0.820294     0.800384   0.81002     0.810339      0.810339
1     recall       0.793981     0.826058   0.81002     0.810020      0.810020
2   f1-score       0.806923     0.813019   0.81002     0.809971      0.809971
3    support    3024.000000  3024.000000   0.81002  6048.000000   6048.000000

Test: Gradient Boosting Classifer


metric  not depressed   depressed  accuracy   macro avg  weighted avg
0  precision       0.933764    0.380769  0.770193    0.657267      0.845688
1     recall       0.782138    0.707143  0.770193    0.744640      0.770193
2   f1-score       0.851252    0.495000  0.770193    0.673126      0.794511
3    support     739.000000  140.000000  0.770193  879.000000    879.000000

## Test Train Grid

In [61]:

params = {
    "gradientboostingclassifier__loss":['log_loss', 'exponential'],#["log_loss", "exponential"],
    "gradientboostingclassifier__learning_rate": [0.1,0.15, 0.2, 0.25, 0.3],#[0.1, 0.15, 0.2, 1, 5],
    # "gradientboostingclassifier__min_samples_split": [1,2,6,12],
    # "gradientboostingclassifier__min_samples_leaf": [0,1,4,8],
    "gradientboostingclassifier__max_depth":[2, 3],
    "gradientboostingclassifier__max_features":[3,9,15,25,None],#["sqrt", None],
    # "gradientboostingclassifier__criterion": ["friedman_mse", "squared_error"],
    "gradientboostingclassifier__subsample":[0.4, 0.7, 0.9],
    "gradientboostingclassifier__n_estimators":[30, 70, 100],
    # "gradientboostingclassifier__warm_start":[True,False],
    # "gradientboostingclassifier__ccp_alpha":[0.0,0.02,0.06]
}


### Train

In [62]:

from sklearn.metrics import make_scorer, fbeta_score

f_beta_score = make_scorer(fbeta_score, beta=1, pos_label=1)
cv_test= KFold(n_splits=3)

grid = GridSearchCV(
    make_pipeline(GradientBoostingClassifier(random_state=42)), 
    param_grid=params, 
    n_jobs=-1, 
    cv=cv_test,#3, 
    verbose=1, 
    scoring=f_beta_score)
    
grid.fit(x_ros, y_ros)

pred_labels = [x.round() for x in grid.best_estimator_.predict(x_ros)]

df_cls_rpt = pd.DataFrame(
    classification_report(
        y_ros, 
        pred_labels, 
        target_names=['not depressed', 'depressed'], 
        output_dict=True
    )
).rename_axis('metric')\
.reset_index()
print('TRAIN: GBC')
print(grid.best_params_)
print(grid.best_score_)


df_cv_results = pd.DataFrame(grid.cv_results_)
print(df_cv_results.iloc[grid.best_index_, :])
df_cls_rpt

Fitting 3 folds for each of 900 candidates, totalling 2700 fits
TRAIN: GBC
{'gradientboostingclassifier__learning_rate': 0.3, 'gradientboostingclassifier__loss': 'log_loss', 'gradientboostingclassifier__max_depth': 3, 'gradientboostingclassifier__max_features': None, 'gradientboostingclassifier__n_estimators': 100, 'gradientboostingclassifier__subsample': 0.7}
0.6948048708087411
mean_fit_time                                                                               0.539596
std_fit_time                                                                                0.016187
mean_score_time                                                                             0.004741
std_score_time                                                                               0.00082
param_gradientboostingclassifier__learning_rate                                                  0.3
param_gradientboostingclassifier__loss                                                      log_loss
param_gradie

metric  not depressed    depressed  accuracy    macro avg  weighted avg
0  precision       0.918268     0.875981  0.895999     0.897124      0.897124
1     recall       0.869378     0.922619  0.895999     0.895999      0.895999
2   f1-score       0.893154     0.898695  0.895999     0.895925      0.895925
3    support    3024.000000  3024.000000  0.895999  6048.000000   6048.000000

### Test

In [63]:
pred_labels = [x.round() for x in grid.best_estimator_.predict(x_test)]

df_cls_rpt = pd.DataFrame(
    classification_report(
        y_test, 
        pred_labels, 
        target_names=['not depressed', 'depressed'], 
        output_dict=True
    )
).rename_axis('metric')\
.reset_index()
print(grid.best_params_)
print(grid.best_score_)


df_cv_results = pd.DataFrame(grid.cv_results_)
print(df_cv_results.iloc[grid.best_index_, :])
df_cls_rpt


{'gradientboostingclassifier__learning_rate': 0.3, 'gradientboostingclassifier__loss': 'log_loss', 'gradientboostingclassifier__max_depth': 3, 'gradientboostingclassifier__max_features': None, 'gradientboostingclassifier__n_estimators': 100, 'gradientboostingclassifier__subsample': 0.7}
0.6948048708087411
mean_fit_time                                                                               0.539596
std_fit_time                                                                                0.016187
mean_score_time                                                                             0.004741
std_score_time                                                                               0.00082
param_gradientboostingclassifier__learning_rate                                                  0.3
param_gradientboostingclassifier__loss                                                      log_loss
param_gradientboostingclassifier__max_depth                                            

metric  not depressed   depressed  accuracy   macro avg  weighted avg
0  precision       0.909639    0.372093  0.778157    0.640866      0.824023
1     recall       0.817321    0.571429  0.778157    0.694375      0.778157
2   f1-score       0.861012    0.450704  0.778157    0.655858      0.795662
3    support     739.000000  140.000000  0.778157  879.000000    879.000000

# log regression

In [46]:
baseline_model_ros = baseline_models(x_ros, y_ros, x_test, y_test, do_smote=False)
baseline_model_ros[['model','precision','recall','f1-score']]

model  precision    recall  f1-score
2  Gradient Boosting Classifier   0.658055  0.745317  0.674169
2           Logistic Regression   0.637796  0.729456  0.644126
2          Gaussian Naive Bayes   0.599621  0.681606  0.575623
2         Bernoulli Naive Bayes   0.601771  0.673255  0.597695
2                           Knn   0.593529  0.643176  0.598552
2                 Decision Tree   0.634275  0.620684  0.626657
2                 Random Forest   0.734144  0.581355  0.600489

In [57]:
lm = LogisticRegression()
lm.fit(x_ros, y_ros)

pred_labels = [x.round() for x in lm.predict(x_ros)]

df_cls_rpt = pd.DataFrame(
    classification_report(
        y_ros, 
        pred_labels, 
        target_names=['not depressed', 'depressed'], 
        output_dict=True
    )
).rename_axis('metric')\
.reset_index()
print('Train: Logistic Regression')
display(df_cls_rpt)


pred_labels = [x.round() for x in lm.predict(x_test)]

df_cls_rpt = pd.DataFrame(
    classification_report(
        y_test, 
        pred_labels, 
        target_names=['not depressed', 'depressed'], 
        output_dict=True
    )
).rename_axis('metric')\
.reset_index()
print('Test: Logistic Regression')
df_cls_rpt

Train: Logistic Regression


metric  not depressed    depressed  accuracy    macro avg  weighted avg
0  precision       0.710602     0.727554   0.71875     0.719078      0.719078
1     recall       0.738095     0.699405   0.71875     0.718750      0.718750
2   f1-score       0.724088     0.713202   0.71875     0.718645      0.718645
3    support    3024.000000  3024.000000   0.71875  6048.000000   6048.000000

Test: Logistic Regression


metric  not depressed   depressed  accuracy   macro avg  weighted avg
0  precision       0.933219    0.342373  0.734926    0.637796      0.839114
1     recall       0.737483    0.721429  0.734926    0.729456      0.734926
2   f1-score       0.823885    0.464368  0.734926    0.644126      0.766624
3    support     739.000000  140.000000  0.734926  879.000000    879.000000

## Test Train Grid

In [51]:
params_lm = {
    'logisticregression__penalty': ['l1','l2', 'elasticnet'], 
    'logisticregression__C': np.linspace(0.004,0.01,21), #[0.001,0.01,0.1,1,10,100,1000],
    'logisticregression__solver' : ['liblinear', 'lbfgs', 'newton-cg', 'newton-cholesky', 'sag', 'saga'], #'liblinear', 
    'logisticregression__multi_class' : ['ovr', 'multinomial'],
    'logisticregression__n_jobs' : [-1],
    'logisticregression__l1_ratio': [0.02, 0.04, 0.06, 0.08, 0.1,0.12, 0.14], #[0.25, 0.35, 0.5, 0.65, 0.75],
    'logisticregression__class_weight': ['balanced', None],
}
{'logisticregression__C': 0.001, 'logisticregression__class_weight': None, 'logisticregression__l1_ratio': 0.65, 'logisticregression__multi_class': 'auto', 'logisticregression__n_jobs': -1, 'logisticregression__penalty': 'elasticnet', 'logisticregression__solver': 'saga'}


{'logisticregression__C': 0.001,
 'logisticregression__class_weight': None,
 'logisticregression__l1_ratio': 0.65,
 'logisticregression__multi_class': 'auto',
 'logisticregression__n_jobs': -1,
 'logisticregression__penalty': 'elasticnet',
 'logisticregression__solver': 'saga'}

In [58]:

from sklearn.metrics import make_scorer, fbeta_score

f_beta_score = make_scorer(fbeta_score, beta=1, pos_label=1)

grid = GridSearchCV(
    make_pipeline(LogisticRegression()), 
    param_grid=params_lm, 
    n_jobs=-1, 
    cv=3, 
    verbose=1, 
    scoring=f_beta_score#'f1_macro'#f_beta_score
)
    #'f1_macro')
    
grid.fit(x_ros, y_ros)

pred_labels = [x.round() for x in grid.best_estimator_.predict(x_ros)]

df_cls_rpt = pd.DataFrame(
    classification_report(
        y_ros, 
        pred_labels, 
        target_names=['not depressed', 'depressed'], 
        output_dict=True
    )
).rename_axis('metric')\
.reset_index()
print('TRAIN: Logistic Regression')
print(grid.best_params_)
df_cls_rpt


Fitting 3 folds for each of 10584 candidates, totalling 31752 fits


/Users/jonhand/Desktop/w210_Capstone/capstone210-ppd-carmeli_chari_hand_lee/.venv/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:1171: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=l1)
  warnings.warn(
/Users/jonhand/Desktop/w210_Capstone/capstone210-ppd-carmeli_chari_hand_lee/.venv/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:1222: UserWarning: 'n_jobs' > 1 does not have any effect when 'solver' is set to 'liblinear'. Got 'n_jobs' = 8.
  warnings.warn(
/Users/jonhand/Desktop/w210_Capstone/capstone210-ppd-carmeli_chari_hand_lee/.venv/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:1171: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=l1)
  warnings.warn(
/Users/jonhand/Desktop/w210_Capstone/capstone210-ppd-carmeli_chari_hand_lee/.venv/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:1222: UserWarning: 'n_jobs' > 1 does not have any effect when

TRAIN: Logistic Regression
{'logisticregression__C': 0.0046, 'logisticregression__class_weight': 'balanced', 'logisticregression__l1_ratio': 0.02, 'logisticregression__multi_class': 'ovr', 'logisticregression__n_jobs': -1, 'logisticregression__penalty': 'l2', 'logisticregression__solver': 'liblinear'}


metric  not depressed    depressed  accuracy    macro avg  weighted avg
0  precision       0.720779     0.706919  0.713624     0.713849      0.713849
1     recall       0.697421     0.729828  0.713624     0.713624      0.713624
2   f1-score       0.708908     0.718191  0.713624     0.713549      0.713549
3    support    3024.000000  3024.000000  0.713624  6048.000000   6048.000000

In [59]:

# grid.fit(x_ros, y_ros)

pred_labels = [x.round() for x in grid.best_estimator_.predict(x_test)]

df_cls_rpt = pd.DataFrame(
    classification_report(
        y_test, 
        pred_labels, 
        target_names=['not depressed', 'depressed'], 
        output_dict=True
    )
).rename_axis('metric')\
.reset_index()
print('TEST: Logistic Regression')
print(grid.best_params_)
df_cv_results = pd.DataFrame(grid.cv_results_)
print(df_cv_results.iloc[grid.best_index_, :])
df_cls_rpt
#{'logisticregression__C': 0.008416666666666666, 'logisticregression__class_weight': None, 'logisticregression__l1_ratio': 0.1, 'logisticregression__multi_class': 'ovr', 'logisticregression__n_jobs': -1, 'logisticregression__penalty': 'l2', 'logisticregression__solver': 'liblinear'}


TEST: Logistic Regression
{'logisticregression__C': 0.0046, 'logisticregression__class_weight': 'balanced', 'logisticregression__l1_ratio': 0.02, 'logisticregression__multi_class': 'ovr', 'logisticregression__n_jobs': -1, 'logisticregression__penalty': 'l2', 'logisticregression__solver': 'liblinear'}
mean_fit_time                                                                      0.006004
std_fit_time                                                                       0.000492
mean_score_time                                                                     0.00341
std_score_time                                                                     0.001987
param_logisticregression__C                                                          0.0046
param_logisticregression__class_weight                                             balanced
param_logisticregression__l1_ratio                                                     0.02
param_logisticregression__multi_class                 

metric  not depressed   depressed  accuracy   macro avg  weighted avg
0  precision       0.936842    0.336570  0.725825    0.636706      0.841236
1     recall       0.722598    0.742857  0.725825    0.732728      0.725825
2   f1-score       0.815890    0.463252  0.725825    0.639571      0.759725
3    support     739.000000  140.000000  0.725825  879.000000    879.000000